In [3]:
import os
if "ntbk" in os.getcwd():
    os.chdir("..")
print(os.getcwd())

import sys
sys.path.append(os.path.join(os.getcwd(), "otgnn"))


%load_ext autoreload
%autoreload 2

from otgnn.models import GCN
from otgnn.graph import MolGraph
from otgnn.utils import save_model, load_model

from mol_opt.mol_opt import MolOpt
from mol_opt.data_mol_opt import MolOptDataset
from mol_opt.data_mol_opt import get_loader
from mol_opt.arguments import get_args
from mol_opt.train_mol_opt import main, get_latest_model
from mol_opt.ot_utils import compute_barycenter

from rdkit.Chem import MolFromSmiles

import torch
import numpy as np
import time
import torch.nn.functional as F

/home/octav/gitrepos/tum-thesis


In [4]:
model_type = "deepsets"
sys.argv = ["", "-cuda", "-model_type", model_type]
args = get_args()
outdir_suffix = "dev4"
args.n_epochs = 20000 
args.init_model = "{}-attention-random-sink3-test1".format(model_type)
# args.init_model = "{}-test1".format(model_type)
args.init_decoder_model = "{}_decode".format(args.init_model)
args.output_dir = "mol_opt/output_{}/{}".format(outdir_suffix, args.init_model)
args.tb_logs_dir = "mol_opt/logs_{}/{}".format(outdir_suffix, args.init_model)
args.batch_size = 50 

args.penalty_gumbel = False 

args.scale_lambdas = True
args.connectivity = True 
args.valency = True 
args.euler_characteristic_penalty = True
args.conn_lambda_start = 0.001
args.conn_lambda_end = 3
args.conn_lambda_epochs_start = 4001
args.conn_lambda_epochs_end = 12000
args.valency_lambda_start = 0.001
args.valency_lambda_end = 5
args.valency_lambda_epochs_start = 4001
args.valency_lambda_epochs_end = 12000
args.euler_lambda_start = 0.001 
args.euler_lambda_end = 2 
args.euler_lambda_epochs_start = 4001
args.euler_lambda_epochs_end = 12000
args.tau_start = 1
args.tau_end = 0.01
args.tau_epochs_start = 1
args.tau_epochs_end = 12000

args.cross_att_use = True
args.cross_att_random = True
args.cross_att_n_sinkhorn = 3
# args.morgan_bits = 1024

args.conn_penalty_function = "capped_logdet" 

print(args, '\n')

Namespace(N_transformer=6, agg_func='sum', batch_norm=False, batch_size=50, conn_lambda_end=3, conn_lambda_epochs_end=12000, conn_lambda_epochs_start=4001, conn_lambda_start=0.001, conn_penalty_function='capped_logdet', connectivity=True, connectivity_hard=False, cross_att_dim=150, cross_att_n_sinkhorn=3, cross_att_random=True, cross_att_use=True, cuda=True, device='cuda:0', dim_tangent_space=40, dropout_ffn=0.0, dropout_gcn=0.0, dropout_transformer=0.1, euler_characteristic_penalty=True, euler_lambda_end=2, euler_lambda_epochs_end=12000, euler_lambda_epochs_start=4001, euler_lambda_start=0.001, ffn_activation='LeakyReLU', init_decoder_model='deepsets-attention-random-sink3-test1_decode', init_model='deepsets-attention-random-sink3-test1', linear_out=False, max_num_atoms=70, model_type='deepsets', morgan_bits=0, n_epochs=20000, n_ffn_hidden=100, n_ffn_transformer=100, n_heads_transformer=10, n_hidden=200, n_labels=1, n_layers=5, one_batch_train=False, ot_solver='emd', output_dir='mol_o

In [5]:
# train_data_loader = get_loader("iclr19-graph2graph/data/qed", "train_pairs", args.batch_size, same_number_atoms = True)
# train_data_loader = get_loader("molgen/data/chembl50", "train", args.batch_size, same_number_atoms = True)
# val_data_loader = get_loader("iclr19-graph2graph/data/qed", "valid", 36, False)

train_data_loader = get_loader("molgen/data/chembl50", "train", args.batch_size, same_number_atoms = True)
# val_data_loader = get_loader("molgen/data/chembl50", "val_split", args.batch_size, same_number_atoms = True)
val_data_loader = None

In [6]:
molopt, molopt_decoder = main(args, train_data_loader = train_data_loader, val_data_loader = val_data_loader)

No model deepsets-attention-random-sink3-test1 found in mol_opt/output_dev4/deepsets-attention-random-sink3-test1! Starting from scratch.
Penalty params: tau=1.00000 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=-1 mode=[0 0 0] conn=True val=True euler=True
Epoch: 1


/home/octav/gitrepos/tum-thesis/otgnn/models/gromov_modules.py:398: UserWarning: Implicit dimension choice for log_softmax has been deprecated. Change the call to include dim=X as an argument.
  nce_reg = torch.nn.LogSoftmax()(torch.stack(all_nce_dists))[0]


Losses Batch 0, train
 fgw:10285.5012500
 conn_penalty:0.0000000
 val_penalty:677.7514062
 euler_penalty:196.6834961
 total:10286.3743750
Penalty params: tau=1.00000 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=1 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=1.00000 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=1 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 1, train
 fgw:10285.5012500
 conn_penalty:0.0000000
 val_penalty:677.7514062
 euler_penalty:196.6834961
 total:10286.3743750
Epoch duration: 3.353282928466797
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-random-sink3-test1/model_deepsets-attention-random-sink3-test1_1
Epoch: 2
Losses Batch 0, train
 fgw:1075148761333.7600098
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:1075148761333.7600098
Penalty params: tau=0.99962 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=2 mode=[0 0 0] conn=False val=False euler=False
Pen

Losses Batch 0, train
 fgw:262299791.3600000
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:262299791.3600000
Penalty params: tau=0.99541 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=13 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.99541 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=13 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 13, train
 fgw:262299791.3600000
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:262299791.3600000
Epoch duration: 0.7421097755432129
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-random-sink3-test1/model_deepsets-attention-random-sink3-test1_13
Epoch: 14
Losses Batch 0, train
 fgw:253013114.8800000
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:253013114.8800000
Penalty params: tau=0.99502 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=14 mode=[0 0 0] conn=False val=False euler=Fa

Losses Batch 0, train
 fgw:323420078.0800000
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:323420078.0800000
Penalty params: tau=0.99083 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=25 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.99083 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=25 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 25, train
 fgw:323420078.0800000
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:323420078.0800000
Epoch duration: 0.7538700103759766
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-random-sink3-test1/model_deepsets-attention-random-sink3-test1_25
Epoch: 26
Losses Batch 0, train
 fgw:277031587.8400000
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:277031587.8400000
Penalty params: tau=0.99045 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=26 mode=[0 0 0] conn=False val=False euler=Fa

...

Losses Batch 0, train
 fgw:32227076341.7599983
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:32227076341.7599983
Penalty params: tau=0.06401 conn_l=0.02370 val_l=0.02900 euler_l=0.02019 epoch=7163 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.06401 conn_l=0.02370 val_l=0.02900 euler_l=0.02019 epoch=7163 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7163, train
 fgw:32227076341.7599983
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:32227076341.7599983
Epoch duration: 4.617673635482788
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-random-sink3-test1/model_deepsets-attention-random-sink3-test1_7163
Epoch: 7164
Losses Batch 0, train
 fgw:33215917588.4799995
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:33215917588.4799995
Penalty params: tau=0.06398 conn_l=0.02372 val_l=0.02903 euler_l=0.02021 epoch=7164 mode=[1 1 1] 

Losses Batch 0, train
 fgw:9789227663.3600006
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:9789227663.3600006
Penalty params: tau=0.06374 conn_l=0.02396 val_l=0.02934 euler_l=0.02040 epoch=7174 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.06374 conn_l=0.02396 val_l=0.02934 euler_l=0.02040 epoch=7174 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7174, train
 fgw:9789227663.3600006
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:9789227663.3600006
Epoch duration: 4.471886396408081
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-random-sink3-test1/model_deepsets-attention-random-sink3-test1_7174
Epoch: 7175
Losses Batch 0, train
 fgw:9543896924.1599998
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:9543896924.1599998
Penalty params: tau=0.06371 conn_l=0.02398 val_l=0.02937 euler_l=0.02042 epoch=7175 mode=[1 1 1] conn=T

Losses Batch 0, train
 fgw:10835108167.6800003
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:10835108167.6800003
Penalty params: tau=0.06347 conn_l=0.02422 val_l=0.02969 euler_l=0.02061 epoch=7185 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.06347 conn_l=0.02422 val_l=0.02969 euler_l=0.02061 epoch=7185 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7185, train
 fgw:10835108167.6800003
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:10835108167.6800003
Epoch duration: 4.663022518157959
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-random-sink3-test1/model_deepsets-attention-random-sink3-test1_7185
Epoch: 7186
Losses Batch 0, train
 fgw:9669551063.0400009
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:9669551063.0400009
Penalty params: tau=0.06345 conn_l=0.02425 val_l=0.02972 euler_l=0.02063 epoch=7186 mode=[1 1 1] co

Losses Batch 0, train
 fgw:5662119690.2399998
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:5662119690.2399998
Penalty params: tau=0.06320 conn_l=0.02449 val_l=0.03004 euler_l=0.02083 epoch=7196 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.06320 conn_l=0.02449 val_l=0.03004 euler_l=0.02083 epoch=7196 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7196, train
 fgw:5662119690.2399998
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:5662119690.2399998
Epoch duration: 4.512800693511963
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-random-sink3-test1/model_deepsets-attention-random-sink3-test1_7196
Epoch: 7197
Losses Batch 0, train
 fgw:7137299660.8000002
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:7137299660.8000002
Penalty params: tau=0.06318 conn_l=0.02452 val_l=0.03007 euler_l=0.02085 epoch=7197 mode=[1 1 1] conn=T

KeyboardInterrupt: 